<a href="https://colab.research.google.com/github/yorkjong/vistock/blob/feature%2Franking_utils/notebooks/ibd_fin.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Stock Analysis and Ranking Inspired by IBD's EPS Rating
#### References
- [Growth Stocks And How To Analyze Earnings Growth: Using IBD's EPS Rating](https://www.investors.com/how-to-invest/investors-corner/growth-stocks-and-how-to-analyze-earnings-growth-using-ibd-eps-rating/)
  - takes a company's two most recent year-over-year changes in quarterly earnings, and the profit of the past three to five years, then compares those results with the thousands of stocks in IBD's database.
- [How To Invest: Check This Rating Before Buying Your Next Stock](https://www.investors.com/how-to-invest/investors-corner/how-to-invest-earnings-growth/)

### Install and Config

#### Install Required Packages

In [1]:
%pip install "git+https://github.com/yorkjong/vistock.git@feature/ranking_utils"
%pip install requests-cache

  Cloning https://github.com/yorkjong/vistock.git (to revision feature/ranking_utils) to /tmp/pip-req-build-pa0catf7
  Running command git clone --filter=blob:none --quiet https://github.com/yorkjong/vistock.git /tmp/pip-req-build-pa0catf7
  Running command git checkout -b feature/ranking_utils --track origin/feature/ranking_utils
  Switched to a new branch 'feature/ranking_utils'
  Branch 'feature/ranking_utils' set up to track remote branch 'feature/ranking_utils' from 'origin'.
  Resolved https://github.com/yorkjong/vistock.git to commit eb3cc9633b9067264fde29ba099b96c0756e8629
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.0/75.0 kB 732.3 kB/s eta 0:00:00
  Created wheel for vistock: filename=vistock-0.7.0-py3-none-any.whl size=89082 sha256=6416f2674329fee89edcd963153a31220b2ea9817a40888a2ab1b7236e6f71b7
  Stored in directory: /tmp/pip-ephem-wheel-cache-x9gxjcp8/wheels/37/13/2b/a599ed1c9af840bb5c5d20b1aa8e13e50523bc0d554a13952d
Successfully 

#### Setup and Configuration

In [2]:
# @title Enable DataFrame Formatter
from google.colab import data_table
data_table.enable_dataframe_formatter()

In [3]:
# @title Enable Requests Cache
import requests_cache
requests_cache.install_cache('ibd_cache', expire_after=3600)

In [4]:
# @title GitHub
import base64
import requests
import pandas as pd
from io import StringIO


class GitHub:
    def __init__(self, repo_owner, repo_name, token, dir='', branch='main'):
        self.base_url = f'https://api.github.com/repos/{repo_owner}/{repo_name}'
        dir = dir.strip('/')
        if dir:
            self.contents_url = f'{self.base_url}/contents/{dir}'
        else:
            self.contents_url = f'{self.base_url}/contents'
        self.branch = branch
        self.token = token

    def _request(self, method, url, headers=None, params=None, json=None):
        response = requests.request(method, url, headers=headers,
                                    params=params, json=json)
        if response.status_code in [200, 201]:
            return response.json()
        elif response.status_code == 404:
            return None
        else:
            print(f"Request failed: {response.status_code} - {response.json()}")
            return None

    def list_branches(self):
        url = f'{self.base_url}/branches'
        headers = {
            'Authorization': f'token {self.token}',
            'Accept': 'application/vnd.github.v3+json'
        }
        response = requests.get(url, headers=headers)
        if response.status_code == 200:
            branches = response.json()
            return [branch['name'] for branch in branches]
        else:
            print(f"Failed to retrieve branches: {response.status_code} - {response.json()}")
            return []
        def branch_exists(self):
            url = f'{self.base_url}/git/refs/heads/{self.branch}'
            headers = {
                'Authorization': f'token {self.token}',
                'Accept': 'application/vnd.github.v3+json',
            }
            response = requests.get(url, headers=headers)
            if response.status_code == 200:
                return True
            elif response.status_code == 404:
                return False
            else:
                print(f"Request failed: {response.status_code} - {response.json()}")
                return None

    def file_exists(self, file_path):
        url = f'{self.contents_url}/{file_path}'
        headers = {
            'Authorization': f'token {self.token}',
            'Accept': 'application/vnd.github.v3+json',
        }
        response = requests.get(url, headers=headers,
                                params={'ref': self.branch})
        if response.status_code == 200:
            return True
        elif response.status_code == 404:
            return False
        else:
            print(f"Request failed: {response.status_code} - {response.json()}")
            return None

    def list_filenames(self, dir_path=''):
        url = f'{self.contents_url}/{dir_path}'
        headers = {
            'Authorization': f'token {self.token}',
            'Accept': 'application/vnd.github.v3+json',
        }
        response = requests.get(url, headers=headers,
                                params={'ref': self.branch})
        if response.status_code == 200:
            files = response.json()
            return [item['name'] for item in files]
        if response.status_code == 404:
            print(f"Directory '{dir_path}' does not exist.")
            return []
        else:
            print(f"Request failed: {response.status_code} - {response.json()}")
            return []

    def download_file(self, file_path):
        url = f'{self.contents_url}/{file_path}'
        headers = {
            'Authorization': f'token {self.token}',
            'Accept': 'application/vnd.github.v3+json',
        }

        file_info = self._request('GET', url, headers=headers,
                                  params={'ref': self.branch})
        if file_info:
            response = requests.get(file_info['download_url'])
            if response.status_code == 200:
                return StringIO(response.text)
            else:
                print(f"Failed to download file: "
                      f"{response.status_code} - {response.text}")
        else:
            print(f"File '{file_path}' does not exist. Cannot download.")
        return None

    def download_csv(self, file_path):
        file_content = self.download_file(file_path)
        if file_content:
            return pd.read_csv(file_content)
        else:
            return pd.DataFrame()

    def upload_file(self, file_path, content):
        url = f'{self.contents_url}/{file_path}'

        # Encode the content to base64
        encoded_content = base64.b64encode(content.encode()).decode()
        payload = {
            'message': 'Uploading file',
            'content': encoded_content,
            'branch': self.branch
        }

        headers = {
            'Authorization': f'token {self.token}',
            'Accept': 'application/vnd.github.v3+json'
        }

        # Check if the file already exists to get the current sha
        file_info = self._request('GET', url, headers=headers,
                                  params={'ref': self.branch})
        # If the file exists, get the current SHA
        if file_info:
            payload['sha'] = file_info.get('sha')

        # PUT request to create or update the file
        self._request('PUT', url, headers=headers, json=payload)

    def upload_df_as_csv(self, file_path, df):
        """Upload a DataFrame to a CSV file."""
        if not file_path.endswith('.csv'):
            file_path += '.csv'
        csv_content = df.to_csv(index=False)
        self.upload_file(file_path, csv_content)

    def remove_file(self, file_path):
        if not self.file_exists(file_path):
            print(f"File '{file_path}' does not exist. Skipping deletion.")
            return

        url = f'{self.contents_url}/{file_path}'
        headers = {
            'Authorization': f'token {self.token}',
            'Accept': 'application/vnd.github.v3+json'
        }

        # Fetch the file info to get the SHA needed for deletion
        file_info = self._request('GET', url, headers=headers)
        if file_info:
            payload = {
                'message': 'Deleting file',
                'sha': file_info['sha'],
                'branch': self.branch
            }
            self._request('DELETE', url, headers=headers, json=payload)

#-------------------------------------------------------------------------------

from google.colab import userdata

github = GitHub(
    repo_owner='yorkjong',
    repo_name='stock-reports',
    token=userdata.get('GithubToken.stock-reports'),
    dir='ibd_fin',
    branch='data'
)


In [5]:
# @title DataFrame Operations

def is_taiwan_stock_df(df):
    ticker = df['Ticker'].iloc[0].replace('.TWO', '').replace('.TW', '')
    return ticker.isdigit()

def add_name_column(df):
    column_names = df.columns.tolist()
    if 'Name' in column_names:
        return df
    if 'Ticker' not in column_names:
        return df
    if df.empty:
        return df
    if not is_taiwan_stock_df(df):
        return df
    df['Name'] = None
    ticker_index = column_names.index('Ticker')
    column_names.insert(ticker_index + 1, 'Name')
    df = df[column_names]   # create a new DataFrame
    df['Name'] = df['Ticker'].apply(tw.stock_name)
    return df


def remove_ticker_suffix(df, ticker_column):
    """
    Remove the '.TW' or '.TWO' suffix from ticker codes in a DataFrame.

    Parameters:
    - df: The DataFrame containing ticker codes.
    - ticker_column: The name of the column containing ticker codes.
    """
    # Apply string replacement for each ticker in the specified column
    df[ticker_column] = df[ticker_column].str.replace('.TWO', '', regex=False)
    df[ticker_column] = df[ticker_column].str.replace('.TW', '', regex=False)


In [6]:
# @title Rank Function

import os
from datetime import datetime

from vistock import ibd_fin as fin
from vistock import tw
from vistock.stock_indices import get_tickers


def remove_failed_tickers(tickers):
    delisted = ['BRK.B', 'LEN.B', 'BF.B', 'UHAL.B', 'BF.A', 'CWEN.A', 'HEI.A']
    invalid = ['GEV', 'SOLV', 'VLTO', 'SW', 'ARM', 'CART', 'AS', 'BIRK', 'VSTS','LOAR', 'ALAB','GRAL', 'SEG']
    invalid += ['00945B.TW', '6928.TW', '6914.TW', '6771.TW', '00944.TW', '8162.TW', '1563.TW', '00946.TW', '00941.TW', '6423.TW', '00940.TW', '00939.TW', '4949.TW', '00943.TW', '8487.TW', '6794.TW', '6949.TW', '4771.TW']
    invalid += ['00936.TW', '6805.TW', '2254.TW', '6658.TW', '00935.TW', '6592B.TW', '6526.TW', '6906.TW', '4736.TW', '00636K.TW', '6968.TWO', '4442.TWO', '6534.TW', '6901.TW', '00934.TW', '00657K.TW', '6472.TW', '2258.TW', '6916.TW', '2762.TW', '6933.TW']
    invalid += ['02001R.TW', '020031.TW', '020039.TW', '020016.TW', '02001L.TW', '020019.TW', '020028.TW', '020020.TW', '02001S.TW', '020018.TW', '020038.TW', '020034.TW', '020011.TW', '020030.TW', '020012.TW', '020036.TW', '020029.TW', '020000.TW', '020015.TW', '020037.TW']
    invalid += ['6890.TW', '00951.TW', '3150.TW', '6957.TW', '00947.TW', '00949.TW']
    invalid += ['6838.TW', '00953B.TW', '00956.TW', '00954.TW']
    return list(set(tickers) - set(delisted) - set(invalid))

def rank(code, out_dir='out'):
    tickers = get_tickers(code)
    #tickers = remove_failed_tickers(tickers)

    rank_stock = fin.financial_metric_ranking(tickers)
    if rank_stock.empty:
        print("Not enough data to generate rankings.")
        return

    rank_stock = add_name_column(rank_stock)

    # Remove the '.TW' or '.TWO' suffix
    remove_ticker_suffix(rank_stock, 'Ticker')

    # Save to CSV
    print("\n\n***")
    os.makedirs(out_dir, exist_ok=True)
    today = datetime.now().strftime('%Y%m%d')
    filename = f'{code}_stocks_fin_{today}.csv'
    github.upload_df_as_csv(filename, rank_stock)
    rank_stock.to_csv(os.path.join(out_dir, filename), index=False)
    print(f'Your "{filename}" is in the "{out_dir}" folder.')
    print("***\n")

    return rank_stock

### EPS RS Rating and Ranking

In [7]:
source = "U.S. Listed Stocks" #@param ["S&P 500", "Dow Jones Industrial Average", "NASDAQ 100", "Russell 1000", "Russell 2000", "PHLX Semiconductor", "U.S. Listed Stocks"]

code_from_name = {
    'S&P 500': 'SPX',
    'Dow Jones Industrial Average': 'DJIA',
    'NASDAQ 100': 'NDX',
    'Russell 1000': 'RUI',
    'Russell 2000': 'RUT',
    'PHLX Semiconductor': 'SOX',
    'U.S. Listed Stocks': 'U.S.Listed',
}

df = rank(code_from_name[source])
data_table.DataTable(df, include_index=False, num_rows_per_page=20)

[****************       34%                      ]  1832 of 5443 info downloaded

ERROR:vistock.yf_utils:
Error fetching data for FFIN: 'NoneType' object is not subscriptable
ERROR:vistock.yf_utils:Error fetching info for FFIN: local variable 'inf' referenced before assignment


[                        0%                      ]  21 of 5442 financials downloaded

ABLV: Financials data is empty, returning NaN-filled DataFrame.


[                        0%                      ]  27 of 5442 financials downloaded

...

ZIONO: Missing fields: ['Basic EPS'] will be filled with NaN.


[**********************100%********************* ]  5416 of 5442 financials downloaded

ZIONP: Missing fields: ['Basic EPS'] will be filled with NaN.


[**********************100%**********************]  5442 of 5442 financials downloaded


info[ADT]['trailingPE']: Infinity
info[ANGI]['trailingPE']: Infinity
info[ASPN]['trailingPE']: Infinity
info[BHRB]['trailingPE']: Infinity
info[EHGO]['trailingPE']: Infinity
info[FSM]['trailingPE']: Infinity
info[GMRE]['trailingPE']: Infinity
info[INN]['trailingPE']: Infinity
info[LOBO]['trailingPE']: Infinity
info[ONIT]['trailingPE']: Infinity
info[RELL]['trailingPE']: Infinity
info[SCNI]['trailingPE']: Infinity
info[SNT]['trailingPE']: Infinity
info[SWAG]['trailingPE']: Infinity


***
Your "U.S.Listed_stocks_fin_20241010.csv" is in the "out" folder.
***



### EPS RS Rating and Ranking for Taiwan Stocks

In [8]:
from vistock import tw

source = "上市+上櫃" #@param ["上市", "上櫃", "上市+上櫃", "興櫃", "全部"]

code_from_name = {
    '上市': 'TWSE',
    '上櫃': 'TPEX',
    '上市+上櫃': 'TWSE+TPEX',
    '興櫃': 'ESB',
    '全部': 'TWSE+TPEX+ESB'
}

df_tw = rank(code_from_name[source])
data_table.DataTable(df_tw, include_index=False, num_rows_per_page=20)

[**********************100%**********************]  2085 of 2085 info downloaded


02001S.TW: Financials data is empty, returning NaN-filled DataFrame.


[                        0%                      ]  5 of 1886 financials downloaded

1101B.TW: Missing fields: ['Basic EPS'] will be filled with NaN.


[***                     6%                      ]  122 of 1886 financials downloaded

...

8349A.TWO: Missing fields: ['Basic EPS'] will be filled with NaN.


[********************** 99%********************* ]  1869 of 1886 financials downloaded

9941A.TW: Missing fields: ['Basic EPS'] will be filled with NaN.


[**********************100%**********************]  1886 of 1886 financials downloaded


info[1781.TWO]['trailingPE']: Infinity
info[2506.TW]['trailingPE']: Infinity
info[3060.TW]['trailingPE']: Infinity


***
Your "TWSE+TPEX_stocks_fin_20241010.csv" is in the "out" folder.
***



### Remove files in GitHub Repository

In [ ]:
# @title CSV Deleter
import re
import ipywidgets as widgets

# Example filenames
with requests_cache.disabled():
    all_filenames = github.list_filenames()

# Function to extract unique dates from filenames
def extract_dates(filenames):
    date_pattern = r'\d{8}'
    dates = set()
    for fn in filenames:
        match = re.search(date_pattern, fn)
        if match:
            dates.add(match.group(0))
    return sorted(dates, reverse=True)  # Sort dates from newest to oldest

# Function to remove a file (replace with your actual implementation)
def remove_file(filename):
    print(f"Removing file: {filename}")
    with requests_cache.disabled():
        github.remove_file(filename)
    all_filenames.remove(filename)

#-------------------------------------------------------------------------------

# Update file selector options based on selected date
def update_file_selector(change):
    def selector_width(filenames):
        max_filename_length = max(len(fn) for fn in filenames)
        return f'{max_filename_length * 10}px'  # 10px width per character

    selected_date = change['new']
    lst_fns = [fn for fn in all_filenames if selected_date in fn]
    file_selector_widget.options = lst_fns
    file_selector_widget.rows = len(file_selector_widget.options)
    file_selector_widget.layout=widgets.Layout(width=selector_width(lst_fns))

# Function to delete selected files
def delete_files(button):
    selected_files = file_selector_widget.value
    for file in selected_files:
        remove_file(file)
    update_widgets()    # Update widgets after deletion

# Update widgets to reflect current state
def update_widgets():
    # Refresh the date selector
    dates = extract_dates(all_filenames)
    selected_date = date_selector_widget.value
    if dates and selected_date not in dates:
        i = date_selector_widget.options.index(selected_date)
        if i > len(dates) - 1:
            selected_date = dates[-1]
        else:
            selected_date = dates[i]
    if dates:
        date_selector_widget.options = dates
        date_selector_widget.value = selected_date
    else:
        file_selector_widget.options = []
        return
    update_file_selector({'new': date_selector_widget.value})

#-------------------------------------------------------------------------------

# Create a widget for selecting dates
def create_date_selector(dates):
    return widgets.Dropdown(
        options=dates,
        value = dates[0] if dates else None,
        description='Date:',
        disabled=False
    )

# Create a widget for selecting files
def create_file_selector(filenames):

    return widgets.SelectMultiple(
        options=[],
        value=[],
        description='Files',
        disabled=False,
    )

# Create widgets
dates = extract_dates(all_filenames)
date_selector_widget = create_date_selector(dates)
file_selector_widget = create_file_selector(all_filenames)
delete_button = widgets.Button(description="Delete Selected Files")
delete_button.on_click(delete_files)

# Initialize the file selector with the latest date
update_widgets()

# Set up the observer to update file selector when date is changed
date_selector_widget.observe(update_file_selector, names='value')

# Display widgets
display(date_selector_widget, file_selector_widget, delete_button)

Dropdown(description='Date:', options=('20241007',), value='20241007')

SelectMultiple(description='Files', layout=Layout(width='340px'), options=('TWSE+TPEX_stocks_fin_20241007.csv'…

Button(description='Delete Selected Files', style=ButtonStyle())